In [1]:
import os
os.getcwd()
%cd ../clone-voice-coqui/
%cd CosyVoice/

/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui
/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/CosyVoice


In [4]:
# !git submodule update --init --recursive
# !pip install -r requirements.txt -i https://mirrors.aliyun.com/pypi/simple/ --trusted-host=mirrors.aliyun.com

In [5]:
import sys
sys.path.append('third_party/Matcha-TTS')
from cosyvoice.cli.cosyvoice import CosyVoice, CosyVoice2
from cosyvoice.utils.file_utils import load_wav
import torchaudio
import IPython.display
import torch
print(sys.executable)

/home/is/lathifgalih-k/miniconda3/envs/cosyvoice/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


failed to import ttsfrd, use wetext instead
/home/is/lathifgalih-k/miniconda3/envs/cosyvoice/bin/python


In [6]:
# !git clone https://github.com/FunAudioLLM/CosyVoice.git
# %cd CosyVoice
# ! git submodule update --init --
os.getcwd()

'/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/CosyVoice'

In [6]:
# ## Download pretrained model
# from modelscope import snapshot_download
# snapshot_download('iic/CosyVoice2-0.5B', local_dir='pretrained_models/CosyVoice2-0.5B')

In [7]:
cosyvoice = CosyVoice2('pretrained_models/CosyVoice2-0.5B', load_jit=False, load_trt=False, load_vllm=False, fp16=False)

/home/is/lathifgalih-k/miniconda3/envs/cosyvoice/lib/python3.10/site-packages/diffusers/models/lora.py:393: FutureWarning: `LoRACompatibleLinear` is deprecated and will be removed in version 1.0.0. Use of `LoRACompatibleLinear` is deprecated. Please switch to PEFT backend by installing PEFT: `pip install peft`.
  deprecate("LoRACompatibleLinear", "1.0.0", deprecation_message)
2025-08-26 23:46:18,856 INFO input frame rate=25
/home/is/lathifgalih-k/miniconda3/envs/cosyvoice/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or train

2025-08-26 23:46:28,730 DEBUG https://www.modelscope.cn:443 "GET /api/v1/models/pengzhendong/wetext/revisions HTTP/1.1" 200 205
2025-08-26 23:46:29,547 DEBUG https://www.modelscope.cn:443 "GET /api/v1/models/pengzhendong/wetext/repo/files?Revision=master&Recursive=True HTTP/1.1" 200 None
2025-08-26 23:46:29,740 DEBUG Starting new HTTPS connection (1): www.modelscope.cn:443


2025-08-26 23:46:31,387 DEBUG https://www.modelscope.cn:443 "GET /api/v1/models/pengzhendong/wetext/revisions HTTP/1.1" 200 205
2025-08-26 23:46:31,732 DEBUG https://www.modelscope.cn:443 "GET /api/v1/models/pengzhendong/wetext/repo/files?Revision=master&Recursive=True HTTP/1.1" 200 None


### TTS for ALS n Stroke for CosyVoice2 - Raw Text

In [ ]:
# Voice cloning menggunakan CosyVoice2 dengan teks dari annotations (RAW Text)
import os
import torchaudio
import re
from cosyvoice.utils.file_utils import load_wav
from IPython.display import Audio, display

def load_annotations(annotation_file):
    """Load annotations and create a mapping from audio file to text"""
    annotations = {}
    with open(annotation_file, 'r', encoding='utf-8') as f:
        for line in f:
            line = line.strip()
            if line:
                parts = line.split('|')
                if len(parts) >= 3:
                    audio_path = parts[0]
                    text = parts[2].strip()
                    # Extract filename from path
                    filename = os.path.basename(audio_path)
                    annotations[filename] = text
    return annotations

def clean_text(text):
    """Remove punctuation from text"""
    # Hanya simpan huruf, angka, dan spasi
    return re.sub(r"[^a-zA-Z0-9\s]", "", text)

def apply_trimming(waveform, sample_rate, speaker_id):
    """Apply speaker-specific trimming based on configuration"""
    trimming_config = {
        # ALS speakers
        "A017": 1.0,
        "A010": 0.3,
        "A014": 0.0,
        "A011": 0.8,
        "A008": 0.5,
        "A002": 0.5,
        "A016": 0.8,
        "A006": 0.5,
        "A015": 0.5,
        # Stroke speakers
        "S001": 0.0,
        "S002": 2.6,
        "S003": 0.0,
        "S005": 0.5,
        "S006": 0.5,
        "S007": 0.0,
        "S008": 0.0,
        "S009": 0.0,
        "S011": 0.0,
        "S012": 1.0,
        "S013": 1.1
    }
    
    trim_duration = trimming_config.get(speaker_id, 0.5)
    start_trim = int(trim_duration * sample_rate)
    
    if start_trim > 0 and start_trim < waveform.shape[1]:
        return waveform[:, start_trim:]
    else:
        return waveform

def generate_cosyvoice_with_annotations():
    """Generate voice cloning using CosyVoice2 with corresponding text from annotations"""
    
    # Load ALS annotations
    als_annotation_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/als_speaker_annotations.txt"
    als_annotations = load_annotations(als_annotation_file)
    
    # Load Stroke annotations
    stroke_annotation_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/stroke_speaker_annotations.txt"
    stroke_annotations = load_annotations(stroke_annotation_file)
    
    # Datasets configuration
    datasets = {
        "ALS": {
            "input_dir": "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/",
            "annotations": als_annotations,
            "default_text": "Even for a British Open, this is different"
        },
        "Stroke": {
            "input_dir": "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/dataset-toronto/Stroke/Input_Audios/",
            "annotations": stroke_annotations,
            "default_text": "Even for a British Open, this is different"
        }
    }
    
    # Base output directory
    base_output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/"
    
    for dataset_name, dataset_config in datasets.items():
        print(f"\n📂 Processing {dataset_name} dataset with CosyVoice2...")
        
        input_audio_dir = dataset_config["input_dir"]
        output_dir = os.path.join(base_output_dir, dataset_name, "CosyVoice2")
        annotations = dataset_config["annotations"]
        
        # Create output directory
        if not os.path.exists(output_dir):
            os.makedirs(output_dir)
        
        # Process each speaker
        if os.path.exists(input_audio_dir):
            for speaker in os.listdir(input_audio_dir):
                speaker_path = os.path.join(input_audio_dir, speaker)
                if os.path.isdir(speaker_path):
                    i = 0
                    for audio_file in os.listdir(speaker_path):
                        if i >= 1:  # Only process 1 file per speaker
                            continue
                        
                        # File selection logic based on dataset and speaker
                        should_process = False
                        if dataset_name == "ALS":
                            if speaker == "A015":
                                # For A015, use pataka files
                                if "pataka" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    should_process = True
                            else:
                                # For other ALS speakers, use normal files
                                if "normal" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    should_process = True
                        else:  # Stroke
                            # For Stroke, use segment_0 files
                            if "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                should_process = True
                        
                        if should_process:
                            i += 1
                            input_audio_path = os.path.join(speaker_path, audio_file)
                            
                            # Determine text to synthesize (prompt text)
                            prompt_text = None
                            
                            # Look for matching annotation
                            if annotations:
                                for annotation_filename, annotation_text in annotations.items():
                                    if audio_file == annotation_filename:
                                        prompt_text = annotation_text
                                        break
                            
                            # If not found, use default text
                            if not prompt_text:
                                prompt_text = dataset_config["default_text"]
                                print(f"⚠️  No annotation found for {audio_file}, using default text")
                            
                            # Clean prompt text
                            prompt_text = clean_text(prompt_text)
                            
                            # Target text to synthesize
                            target_text = prompt_text
                            
                            try:
                                print(f"🎯 Processing {speaker}/{audio_file}")
                                print(f"📝 Prompt text: '{prompt_text}'")
                                print(f"🔊 Target text: '{target_text}'")
                                
                                # Load audio reference
                                rev_audio = load_wav(input_audio_path, 16000)
                                print(f"Audio loaded: {rev_audio.shape}")
                                
                                # Perform voice cloning
                                output = cosyvoice.inference_zero_shot(
                                    tts_text=target_text,
                                    prompt_text=prompt_text,
                                    prompt_speech_16k=rev_audio,
                                    stream=False,
                                    text_frontend=False,
                                )
                                
                                # Save and trim results
                                for result_idx, result in enumerate(output):
                                    # Apply speaker-specific trimming
                                    trimmed_waveform = apply_trimming(
                                        result['tts_speech'], 
                                        cosyvoice.sample_rate, 
                                        speaker
                                    )
                                    
                                    # Generate output filename
                                    output_file = os.path.join(output_dir, f"{speaker}_cloned.wav")
                                    
                                    # Save trimmed audio
                                    torchaudio.save(output_file, trimmed_waveform, cosyvoice.sample_rate)
                                    print(f"✅ {speaker} -> saved to '{output_file}'")
                                    
                                    # Optional: display audio
                                    display(Audio(trimmed_waveform, rate=cosyvoice.sample_rate))
                                    
                            except Exception as e:
                                print(f"❌ Error processing {speaker}/{audio_file}: {str(e)}")
        else:
            print(f"⚠️  Input directory not found: {input_audio_dir}")

    print("\n🎉 CosyVoice2 voice cloning with RAW text completed!")

# Run the generation
generate_cosyvoice_with_annotations()


📂 Processing ALS dataset with CosyVoice2...
🎯 Processing A011/input_A011_02_BBP_NORMAL_segment_0.wav
📝 Prompt text: 'Buy Bobby a puppy Buy Bobby a puppy'
🔊 Target text: 'Buy Bobby a puppy Buy Bobby a puppy'
Audio loaded: torch.Size([1, 64000])


  0%|          | 0/1 [00:00<?, ?it/s]

2025-08-26 12:14:03,830 INFO synthesis text Buy Bobby a puppy Buy Bobby a puppy
2025-08-26 12:14:06,837 INFO yield speech len 5.72, rtf 0.5256440256025408


✅ A011 -> saved to '/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/ALS/CosyVoice2/A011_cloned.wav'


100%|██████████| 1/1 [00:03<00:00,  3.39s/it]


...

🎯 Processing S012/input_S012_02_BBP_NORMAL_segment_0.wav
📝 Prompt text: 'Bobby a puppy by bobby a puppy by bobby a puppy'
🔊 Target text: 'Bobby a puppy by bobby a puppy by bobby a puppy'
Audio loaded: torch.Size([1, 85215])


  0%|          | 0/1 [00:00<?, ?it/s]2025-08-26 12:15:08,082 INFO synthesis text Bobby a puppy by bobby a puppy by bobby a puppy
2025-08-26 12:15:10,920 INFO yield speech len 6.08, rtf 0.46677950181459127


✅ S012 -> saved to '/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/Stroke/CosyVoice2/S012_cloned.wav'


100%|██████████| 1/1 [00:04<00:00,  4.28s/it]


🎉 CosyVoice2 voice cloning with RAW text completed!


### Evaluation using SECS for CosyVoice2 - Raw Data (BBP, Pataka, Pa)

In [ ]:
from resemblyzer import VoiceEncoder, preprocess_wav
from pathlib import Path
import numpy as np
from scipy.spatial.distance import cosine
import os
import pandas as pd

# Initialize encoder
encoder = VoiceEncoder()

def evaluate_speaker_similarity(dataset_type):
    """
    Evaluate speaker similarity for ALS or Stroke dataset
    """
    results = []
    
    if dataset_type == "ALS":
        input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/"
        output_base_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/ALS/"
        models = {
            "CosyVoice2": "CosyVoice2/"
        }
    else:  # Stroke
        input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/dataset-toronto/Stroke/Input_Audios/"
        output_base_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/Stroke/"

        models = {
            "CosyVoice2": "CosyVoice2/"
        }
    
    for model_name, model_path in models.items():
        output_dir = os.path.join(output_base_dir, model_path)
        print(f"\n=== Evaluating {dataset_type} - {model_name} ===")
        
        # Get all cloned audio files
        if os.path.exists(output_dir):
            if model_name == "CosyVoice2":
                cloned_files = [f for f in os.listdir(output_dir) if f.endswith("_cloned.wav")]
            else:  # CosyVoice2_Trimmed
                cloned_files = [f for f in os.listdir(output_dir) if f.endswith("_trimmed.wav")]
            
            for cloned_file in cloned_files:
                # Extract speaker ID
                if model_name == "CosyVoice2":
                    speaker_id = cloned_file.replace("_cloned.wav", "")
                else:
                    speaker_id = cloned_file.split("_")[0]
                
                # Find corresponding original audio
                speaker_input_dir = os.path.join(input_audio_dir, speaker_id)
                
                if os.path.exists(speaker_input_dir):
                    original_file = None
                    for audio_file in os.listdir(speaker_input_dir):
                        if dataset_type == "ALS":
                            if speaker_id == "A015":
                                if "pataka" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    original_file = os.path.join(speaker_input_dir, audio_file)
                                    break
                            else:
                                if "normal" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    original_file = os.path.join(speaker_input_dir, audio_file)
                                    break
                        else:  # Stroke
                            if "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                original_file = os.path.join(speaker_input_dir, audio_file)
                                break
                    
                    if original_file and os.path.exists(original_file):
                        try:
                            original_audio = preprocess_wav(Path(original_file))
                            cloned_audio_path = os.path.join(output_dir, cloned_file)
                            cloned_audio = preprocess_wav(Path(cloned_audio_path))
                            
                            original_embed = encoder.embed_utterance(original_audio)
                            cloned_embed = encoder.embed_utterance(cloned_audio)
                            
                            cos_sim = 1 - cosine(original_embed, cloned_embed)
                            
                            results.append({
                                'Dataset': dataset_type,
                                'Model': model_name,
                                'Speaker': speaker_id,
                                'Cosine_Similarity': cos_sim,
                                'Original_File': os.path.basename(original_file),
                                'Cloned_File': cloned_file
                            })
                            
                            print(f"✅ {speaker_id}: {cos_sim:.4f}")
                        except Exception as e:
                            print(f"❌ Error processing {speaker_id}: {str(e)}")
                    else:
                        print(f"⚠️  Original file not found for {speaker_id}")
                else:
                    print(f"⚠️  Speaker directory not found: {speaker_id}")
        else:
            print(f"⚠️  Output directory not found: {output_dir}")
    
    return results

# Run evaluations
print("🔍 Evaluating ALS Dataset...")
als_results = evaluate_speaker_similarity("ALS")

print("\n🔍 Evaluating Stroke Dataset...")
stroke_results = evaluate_speaker_similarity("Stroke")

# Combine results
all_results = als_results + stroke_results
df_results = pd.DataFrame(all_results)

print("\n📊 Summary Results:")
print(df_results)

if not df_results.empty:
    print("\n📈 Average Cosine Similarity by Dataset and Model:")
    summary = df_results.groupby(['Dataset', 'Model'])['Cosine_Similarity'].agg(['mean', 'std', 'count']).round(4)
    print(summary)

    # Save results to CSV
    output_csv = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/RAW/speaker_similarity_evaluation_cosyvoice.csv"
    df_results.to_csv(output_csv, index=False)
    print(f"\n💾 Results saved to: {output_csv}")

else:
    print("⚠️  No results to display")

Loaded the voice encoder model on cuda in 0.02 seconds.
🔍 Evaluating ALS Dataset...

=== Evaluating ALS - CosyVoice2 ===
✅ A016: 0.8953
✅ A011: 0.8989
✅ A002: 0.8989
✅ A014: 0.9255
✅ A008: 0.8993
✅ A015: 0.8651
✅ A006: 0.9191
✅ A010: 0.9436
✅ A017: 0.9382

🔍 Evaluating Stroke Dataset...

=== Evaluating Stroke - CosyVoice2 ===
✅ S005: 0.9415
✅ S013: 0.7566
✅ S009: 0.9509
✅ S002: 0.7206
✅ S011: 0.9152
✅ S007: 0.8841
✅ S001: 0.8746
✅ S006: 0.8686
✅ S008: 0.9238
✅ S003: 0.9330
✅ S012: 0.8527

📊 Summary Results:
   Dataset       Model Speaker  Cosine_Similarity  \
0      ALS  CosyVoice2    A016           0.895321   
1      ALS  CosyVoice2    A011           0.898882   
2      ALS  CosyVoice2    A002           0.898938   
3      ALS  CosyVoice2    A014           0.925470   
4      ALS  CosyVoice2    A008           0.899328   
5      ALS  CosyVoice2    A015           0.865068   
6      ALS  CosyVoice2    A006           0.919110   
7      ALS  CosyVoice2    A010           0.943571   
8      ALS

: 

### Evaluation using SECS for CosyVoice2 - VCTK Data

In [22]:
from resemblyzer import VoiceEncoder, preprocess_wav
from pathlib import Path
import numpy as np
from scipy.spatial.distance import cosine
import os
import pandas as pd

# Initialize encoder
encoder = VoiceEncoder()

def evaluate_speaker_similarity(dataset_type):
    """
    Evaluate speaker similarity for ALS or Stroke dataset
    """
    results = []
    
    if dataset_type == "ALS":
        input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/"
        output_base_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/ALS/"
        # Als use only trimmed
        models = {
            "CosyVoice2": "CosyVoice2/"
        }
    else:  # Stroke
        input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/dataset-toronto/Stroke/Input_Audios/"
        output_base_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/Stroke/"
        # Stroke use raw and trimmed
        models = {
            "CosyVoice2": "CosyVoice2/pre_processing",
            "CosyVoice2_Trimmed": "CosyVoice2/post_processing_trimmed"
        }
    
    for model_name, model_path in models.items():
        output_dir = os.path.join(output_base_dir, model_path)
        print(f"\n=== Evaluating {dataset_type} - {model_name} ===")
        
        # Get all cloned audio files
        if os.path.exists(output_dir):
            if model_name == "CosyVoice2":
                cloned_files = [f for f in os.listdir(output_dir) if f.endswith("_cloned.wav")]
            else:  # CosyVoice2_Trimmed
                cloned_files = [f for f in os.listdir(output_dir) if f.endswith("_trimmed.wav")]
            
            for cloned_file in cloned_files:
                # Extract speaker ID
                if model_name == "CosyVoice2":
                    speaker_id = cloned_file.replace("_cloned.wav", "")
                else:
                    speaker_id = cloned_file.split("_")[0]
                
                # Find corresponding original audio
                speaker_input_dir = os.path.join(input_audio_dir, speaker_id)
                
                if os.path.exists(speaker_input_dir):
                    original_file = None
                    for audio_file in os.listdir(speaker_input_dir):
                        if dataset_type == "ALS":
                            if speaker_id == "A015":
                                if "pataka" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    original_file = os.path.join(speaker_input_dir, audio_file)
                                    break
                            else:
                                if "normal" in audio_file.lower() and "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                    original_file = os.path.join(speaker_input_dir, audio_file)
                                    break
                        else:  # Stroke
                            if "segment_0" in audio_file.lower() and audio_file.endswith(".wav"):
                                original_file = os.path.join(speaker_input_dir, audio_file)
                                break
                    
                    if original_file and os.path.exists(original_file):
                        try:
                            original_audio = preprocess_wav(Path(original_file))
                            cloned_audio_path = os.path.join(output_dir, cloned_file)
                            cloned_audio = preprocess_wav(Path(cloned_audio_path))
                            
                            original_embed = encoder.embed_utterance(original_audio)
                            cloned_embed = encoder.embed_utterance(cloned_audio)
                            
                            cos_sim = 1 - cosine(original_embed, cloned_embed)
                            
                            results.append({
                                'Dataset': dataset_type,
                                'Model': model_name,
                                'Speaker': speaker_id,
                                'Cosine_Similarity': cos_sim,
                                'Original_File': os.path.basename(original_file),
                                'Cloned_File': cloned_file
                            })
                            
                            print(f"✅ {speaker_id}: {cos_sim:.4f}")
                        except Exception as e:
                            print(f"❌ Error processing {speaker_id}: {str(e)}")
                    else:
                        print(f"⚠️  Original file not found for {speaker_id}")
                else:
                    print(f"⚠️  Speaker directory not found: {speaker_id}")
        else:
            print(f"⚠️  Output directory not found: {output_dir}")
    
    return results

# Run evaluations
print("🔍 Evaluating ALS Dataset...")
als_results = evaluate_speaker_similarity("ALS")

print("\n🔍 Evaluating Stroke Dataset...")
stroke_results = evaluate_speaker_similarity("Stroke")

# Combine results
all_results = als_results + stroke_results
df_results = pd.DataFrame(all_results)

print("\n📊 Summary Results:")
print(df_results)

if not df_results.empty:
    print("\n📈 Average Cosine Similarity by Dataset and Model:")
    summary = df_results.groupby(['Dataset', 'Model'])['Cosine_Similarity'].agg(['mean', 'std', 'count']).round(4)
    print(summary)

    # Save results to CSV
    output_csv = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/speaker_similarity_evaluation_cosyvoice.csv"
    df_results.to_csv(output_csv, index=False)
    print(f"\n💾 Results saved to: {output_csv}")

else:
    print("⚠️  No results to display")

Loaded the voice encoder model on cuda in 0.04 seconds.
🔍 Evaluating ALS Dataset...

=== Evaluating ALS - CosyVoice2 ===
✅ A016: 0.8063
✅ A011: 0.8232
✅ A014: 0.8565
✅ A002: 0.8718
✅ A015: 0.8113
✅ A008: 0.8044
✅ A010: 0.8683
✅ A006: 0.8822
✅ A017: 0.7856

🔍 Evaluating Stroke Dataset...

=== Evaluating Stroke - CosyVoice2 ===
✅ S001: 0.6158
✅ S006: 0.7411
✅ S003: 0.8402
✅ S008: 0.7917
✅ S012: 0.8852
✅ S013: 0.8197
✅ S005: 0.8271
✅ S002: 0.6358
✅ S009: 0.8046
✅ S007: 0.8338
✅ S011: 0.7534

=== Evaluating Stroke - CosyVoice2_Trimmed ===
✅ S013: 0.8104
✅ S007: 0.8338
✅ S002: 0.5403
✅ S011: 0.7534
✅ S005: 0.8269
✅ S009: 0.8046
✅ S008: 0.7917
✅ S003: 0.8402
✅ S006: 0.7594
✅ S001: 0.6158
✅ S012: 0.8618

📊 Summary Results:
   Dataset               Model Speaker  Cosine_Similarity  \
0      ALS          CosyVoice2    A016           0.806300   
1      ALS          CosyVoice2    A011           0.823192   
2      ALS          CosyVoice2    A014           0.856527   
3      ALS          CosyVoice2

## VCTK-Dataset

### ALS

#### Example use of Cosyvoice2 for ALS

In [ ]:
# # Simple zero-shot voice cloning dengan CosyVoice2
# import os
# import torchaudio

# # Path input dan output
# input_audio = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/A002/input_A002_02_BBP_NORMAL_segment_0.wav"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/exp/ALS/CosyVoice2"
# os.makedirs(output_dir, exist_ok=True)

# # Text yang akan disintetis
# text_to_clone = "Buy Bobby a puppy."

# print(f"Input audio: {input_audio}")
# print(f"Text to synthesize: {text_to_clone}")

# # Load audio referensi
# rev_audio = load_wav(input_audio, 16000)
# print(f"Audio loaded: {rev_audio.shape}")

# # Lakukan inference
# output = cosyvoice.inference_zero_shot(
#     tts_text=text_to_clone,
#     prompt_text="Buy Bobby a puppy. Buy Bobby a puppy. Buy Bobby.",
#     prompt_speech_16k=rev_audio,
#     stream=False,
#     text_frontend=False,
# )

# # Simpan hasil
# for i, result in enumerate(output):
#     output_file = f'{output_dir}/A002_BBP_cloned.wav'
#     torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#     print(f"Saved: {output_file}")
    
#     # Play audio (opsional)
#     from IPython.display import Audio, display
#     display(Audio(output_file))

# print("Voice cloning selesai!")

#### Voice cloning CosyVoice2 to VCTK text synthesis for ALS

In [ ]:
# import os
# import torchaudio
# from cosyvoice.utils.file_utils import load_wav

# # Path ke direktori input audio dan file annotations
# input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/"
# annotations_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/filelists/als_speaker_annotations.txt"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/"
# os.makedirs(output_dir, exist_ok=True)

# def load_speaker_texts(annotations_file):
#     """Load teks untuk setiap speaker dari annotations file"""
#     pathname_texts = {}
#     prefix = "/home/is/lathifgalih-k/research_naist/multimodal-clone/"
#     with open(annotations_file, 'r', encoding='utf-8') as f:
#         for line in f:
#             if line.strip() and "segment_0" in line:
#                 if "A015" in line and "PATAKA" in line.upper():
#                     parts = line.strip().split('|')
#                     if len(parts) >= 3:
#                         audio_path = parts[0]
#                         text = parts[2].strip()
                        
#                         pathname = os.path.join(prefix,audio_path)
#                         print(f"Processing {pathname} with text: {text}")
#                         # Simpan teks untuk speaker
#                         if pathname not in pathname_texts:
#                             pathname_texts[pathname] = text.replace(',', '').replace('.', '').strip()

#                 elif "NORMAL" in line.upper():
#                     parts = line.strip().split('|')
#                     if len(parts) >= 3:
#                         audio_path = parts[0]
#                         text = parts[2].strip()
                        
#                         pathname = os.path.join(prefix,audio_path)
#                         print(f"Processing {pathname} with text: {text}")
#                         # Simpan teks untuk speaker
#                         if pathname not in pathname_texts:
#                             pathname_texts[pathname] = text.replace(',', '').replace('.', '').strip()
#     return pathname_texts

# # Load teks untuk setiap speaker
# print("📚 Loading speaker texts...")
# pathname_texts = load_speaker_texts(annotations_file)
# print(f"Loaded texts for {len(pathname_texts)} speakers")

In [9]:
# from IPython.display import Audio, display
# for pathname, text in pathname_texts.items():
#     # Load audio referensia
#     rev_audio = load_wav(pathname, 16000)
#     print(f"Audio loaded: {pathname} for {text}")

#     # Lakukan inference
#     output = cosyvoice.inference_zero_shot(
#         tts_text="Even for a British Open, this is different",
#         prompt_text=text,
#         prompt_speech_16k=rev_audio,
#         stream=False,
#         text_frontend=False,
#     )

#     for i, result in enumerate(output):
#         # display audio output
#         output_file = os.path.join(output_dir, f"{os.path.basename(pathname).split('_')[1]}_cloned.wav")
#         display(Audio(result['tts_speech'], rate=cosyvoice.sample_rate))
#         # Save the audio file
#         torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#         print(f"Saved: {output_file}")

#### Postprocessing data syntesis (trimmed) for ALS

In [ ]:
# input_folder = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/ALS/CosyVoice2/"

# for filename in os.listdir(input_folder):
#     if filename.endswith(".wav"):
#         file_path = os.path.join(input_folder, filename)
#         waveform, sample_rate = torchaudio.load(file_path)
        
#         # conditional trimming base on the filename
#         start_trim = 0
#         if "A017" in filename:
#             start_trim = 1 * sample_rate  # 1 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A010" in filename:
#             start_trim = 0.3 * sample_rate  # 0.3 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A014" in filename:
#             start_trim = 0 * sample_rate  # 0 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             from IPython.display import Audio, display
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A011" in filename:
#             start_trim = 0.8 * sample_rate  # 0.3 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A008" in filename:
#             start_trim = 0.5 * sample_rate  # 0.5 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             from IPython.display import Audio, display
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A002" in filename:
#             start_trim = 0.5 * sample_rate  # 0.5 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A016" in filename:
#             start_trim = 0.8 * sample_rate  # 0.8 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             from IPython.display import Audio, display
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A006" in filename:
#             start_trim = 0.5 * sample_rate  # 0.5 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         elif "A015" in filename:
#             start_trim = 0.5 * sample_rate  # 0.5 seconds

#             start_trim = int(start_trim)
#             print(start_trim)
#             print(waveform)
#             trimmed_waveform = waveform[:, start_trim:]

#             # Save the trimmed audio
#             torchaudio.save(file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {file_path}")
#             # Optionally, play the trimmed audio
#             from IPython.display import Audio, display
#             display(Audio(trimmed_waveform, rate=sample_rate))
        


### Stroke

#### Example use of cosyvoice for Stroke

In [17]:
# # # Simple zero-shot voice cloning dengan CosyVoice2 for Stroke dataset
# import os
# import torchaudio

# # Path input dan output
# input_audio = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/dataset-toronto/Stroke/Input_Audios/S003/input_S003_02_BBP_NORMAL_segment_1.wav"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/exp/Stroke/CosyVoice2/"
# os.makedirs(output_dir, exist_ok=True)

# # Text yang akan disintetis
# text_to_clone = "Buy Bobby a puppy."

# print(f"Input audio: {input_audio}")
# print(f"Text to synthesize: {text_to_clone}")

# # Load audio referensi
# rev_audio = load_wav(input_audio, 16000)
# print(f"Audio loaded: {rev_audio.shape}")

# # Lakukan inference
# output = cosyvoice.inference_zero_shot(
#     tts_text=text_to_clone,
#     prompt_text="Buy Bobby a puppy. Buy Bobby a puppy. Buy Bobby a  pup.",
#     prompt_speech_16k=rev_audio,
#     stream=False,
#     text_frontend=False,
# )

# # Simpan hasil
# for i, result in enumerate(output):
#     output_file = f'{output_dir}/S003_BBP_cloned.wav'
#     start_trim = int(0.5 * cosyvoice.sample_rate)
#     result['tts_speech'] = result['tts_speech'][:, start_trim:]
#     torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#     print(f"Saved: {output_file}")

#     # Play audio (opsional)
#     from IPython.display import Audio, display
#     display(Audio(output_file))

# print("Voice cloning selesai!")

#### Make transcribe for stroke audio dataset

In [5]:
# import os
# import torchaudio
# import whisper
# from cosyvoice.utils.file_utils import load_wav
# from IPython.display import Audio, display

# # Check dan load Whisper model (sudah ada dari cell sebelumnya)
# whisper_model = whisper.load_model("large-v2", device="cuda" if torch.cuda.is_available() else "cpu")

In [6]:
# # Voice cloning dataset Stroke menggunakan CosyVoice2 dengan teks dari Whisper
# def extract_text_with_whisper(audio_path):
#     """Ekstraksi teks dari audio menggunakan Whisper"""
#     try:
#         result = whisper_model.transcribe(audio_path)
#         text = result["text"].strip()
#         return text if text else "Even for a British Open, this is different"  # fallback text
#     except Exception as e:
#         print(f"Whisper transcription failed for {audio_path}: {e}")
#         return "Even for a British Open, this is different"  # fallback text

# def load_stroke_speakers_with_whisper(input_audio_dir):
#     """Load semua speaker Stroke dan extract teks dengan Whisper"""
#     speaker_data = {}
    
#     for speaker_folder in sorted(os.listdir(input_audio_dir)):
#         speaker_path = os.path.join(input_audio_dir, speaker_folder)
#         if os.path.isdir(speaker_path):
#             print(f"\nProcessing speaker: {speaker_folder}")
            
#             # Cari file segment_0.wav untuk setiap speaker
#             for audio_file in sorted(os.listdir(speaker_path)):
#                 if "segment_0" in audio_file and audio_file.endswith(".wav"):
#                     full_audio_path = os.path.join(speaker_path, audio_file)
                    
#                     print(f"Processing: {audio_file}")
#                     print("Extracting text with Whisper...")
                    
#                     # Extract teks menggunakan Whisper
#                     extracted_text = extract_text_with_whisper(full_audio_path)
                    
#                     speaker_data[speaker_folder] = {
#                         'audio_path': full_audio_path,
#                         'text': extracted_text.replace(',', '').replace('.', '').strip()
#                     }
                    
#                     print(f"Extracted text: '{extracted_text}'")
#                     break
                
    
#     return speaker_data

# # Path ke direktori input audio Stroke
# input_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/Stroke/Input_Audios/"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/Stroke/CosyVoice2/"
# output_list_path = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/Stroke/stroke_speaker_annotations.txt"
# os.makedirs(output_dir, exist_ok=True)
# os.makedirs(os.path.dirname(output_list_path), exist_ok=True)

# # Load speaker data dengan Whisper transcription
# print("Loading Stroke speakers with Whisper transcription...")
# speaker_data = load_stroke_speakers_with_whisper(input_audio_dir)
# print(f"Loaded {len(speaker_data)} speakers: {list(speaker_data.keys())}")

In [7]:
# # Mapping speaker id to 0-based index
# speaker_mapping = {speaker_id: idx for idx, speaker_id in enumerate(speaker_data.keys())}
# print("Speaker mapping:", speaker_mapping)

# # Simpan data speaker ke file
# print(f"Saving speaker data to {output_list_path}...")
# with open(output_list_path, 'w', encoding='utf-8') as f:
#     for speaker_id, data in speaker_data.items():
#         audio_data = data['audio_path']
#         text_data = data['text']
#         f.write(f"{audio_data}|{speaker_mapping[speaker_id]}|{text_data}\n")

# print(f"Speaker data saved to {output_list_path}")

#### Voice cloning CosyVoice2 to VCTK text synthesis for Stroke

In [8]:
# # Configuration
# text_to_clone = "Even for a British Open, this is different"

# # Voice cloning menggunakan CosyVoice2
# print(f"\n🔊 Starting voice cloning with CosyVoice2...")
# print(f"🎯 Target text: '{text_to_clone}'")
# with open(output_list_path, 'r', encoding='utf-8') as f:
#     lines = f.readlines()
#     lines = [line.strip() for line in lines if line.strip()]
#     print(f"📂 Loaded {len(lines)} audio files for processing")
#     for line in lines:
#         audio_path = line.split('|')[0]
#         text = line.split('|')[2]
#         print(f"📂 Audio loaded: {audio_path}")
#         print(f"📝 Prompt text: {text}")
#         # Load audio referensi
#         rev_audio = load_wav(audio_path, 16000)
#         print(f"Audio loaded: {audio_path} for {text}")
#         # Lakukan inference
#         output = cosyvoice.inference_zero_shot(
#             tts_text=text_to_clone,
#             prompt_text=text,
#             prompt_speech_16k=rev_audio,
#             stream=False,
#             text_frontend=False,
#         )

#         for i, result in enumerate(output):
#             # Save the audio file
#             output_file = os.path.join(output_dir, f"{os.path.basename(audio_path).split('_')[1]}_cloned.wav")
#             torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#             print(f"Saved: {output_file}")
            
#             # Optionally, play the audio
#             display(Audio(output_file, rate=cosyvoice.sample_rate))

# print("\n🎉 Voice cloning untuk dataset Stroke selesai!")
# print(f"📊 Processed {len(lines)} speakers")
# print(f"📁 Results saved in: {output_dir}")

In [9]:
# ### Perbaikan ulang untuk zero-shot voice yang rusak S012 dan S013
# # Configuration
# text_to_clone = "Even for a British Open, this is different"

# # Voice cloning menggunakan CosyVoice2
# print(f"\n🔊 Starting voice cloning with CosyVoice2...")
# print(f"🎯 Target text: '{text_to_clone}'")
# with open(output_list_path, 'r', encoding='utf-8') as f:
#     lines = f.readlines()
#     lines = [line.strip() for line in lines if line.strip()]
#     print(f"📂 Loaded {len(lines)} audio files for processing")
#     for line in lines:
#         audio_path = line.split('|')[0]
#         text = line.split('|')[2]
#         if "S006" not in audio_path:
#             continue
#         print(f"📂 Audio loaded: {audio_path}")
#         print(f"📝 Prompt text: {text}")
#         # Load audio referensi
#         rev_audio = load_wav(audio_path, 16000)
#         print(f"Audio loaded: {audio_path} for {text}")
#         # Lakukan inference
#         output = cosyvoice.inference_zero_shot(
#             tts_text=text_to_clone,
#             prompt_text=text,
#             prompt_speech_16k=rev_audio,
#             stream=False,
#             text_frontend=False,
#         )

#         for i, result in enumerate(output):
#             # Save the audio file
#             output_file = os.path.join(output_dir, f"{os.path.basename(audio_path).split('_')[1]}_cloned.wav")
#             torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#             print(f"Saved: {output_file}")
            
#             # Optionally, play the audio
#             display(Audio(output_file, rate=cosyvoice.sample_rate))

# print("\n🎉 Voice cloning untuk dataset Stroke selesai!")
# print(f"📊 Processed {len(lines)} speakers")
# print(f"📁 Results saved in: {output_dir}")


#### Post-processing trimming untuk hasil cloning Stroke

In [ ]:
# import os
# import torchaudio
# from IPython.display import Audio, display

# input_folder = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/Stroke/CosyVoice2/pre_processing"
# output_folder = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/VCTK/Stroke/CosyVoice2/post_processing_trimmed"

# # Buat direktori output jika belum ada
# os.makedirs(output_folder, exist_ok=True)

# # Konfigurasi trimming untuk speaker Stroke (disesuaikan dengan kebutuhan)
# trimming_config = {
#     "S001": 0, 
#     "S002": 2.6, 
#     "S003": 0,
#     "S005": 0.5,
#     "S006": 0.5,
#     "S007": 0,
#     "S008": 0,
#     "S009": 0,
#     "S011": 0,
#     "S012": 1,
#     "S013": 1.1,
# }

# print("Starting post-processing trimming untuk dataset Stroke...")

# for filename in os.listdir(input_folder):
#     if filename.endswith("_cloned.wav"):
#         input_file_path = os.path.join(input_folder, filename)
        
#         # Extract speaker ID from filename (e.g., "S001_cloned.wav" -> "S001")
#         speaker_id = filename.replace("_cloned.wav", "")
        
#         # Load original audio
#         waveform, sample_rate = torchaudio.load(input_file_path)
        
#         # Get trimming configuration (default 0.5 detik jika speaker tidak ada di config)
#         trim_duration = trimming_config.get(speaker_id, 0.5)
#         start_trim = int(trim_duration * sample_rate)
        
#         print(f"Processing {filename} - Speaker: {speaker_id}, Trim: {trim_duration}s")
        
#         # Create output filename
#         output_filename = f"{speaker_id}_cloned_trimmed.wav"
#         output_file_path = os.path.join(output_folder, output_filename)
        
#         # Apply trimming
#         if start_trim > 0 and start_trim < waveform.shape[1]:
#             trimmed_waveform = waveform[:, start_trim:]
            
#             # Save trimmed audio to new file
#             torchaudio.save(output_file_path, trimmed_waveform, sample_rate)
#             print(f"✅ Trimmed and saved: {output_file_path}")
            
#             # Display trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         else:
#             # No trimming needed or invalid trim duration, copy original file
#             torchaudio.save(output_file_path, waveform, sample_rate)
#             print(f"⚠️ No trimming applied, copied: {output_file_path}")
            
#             # Display original audio
#             display(Audio(waveform, rate=sample_rate))

# print("Post-processing trimming untuk dataset Stroke completed!")
# print(f"📁 Trimmed files saved to: {output_folder}")

### Experiment Use of CosyVoice2

In [15]:
# ## Zero Shot voice cloning with speed input wav
# import torchaudio
# import torch
# import librosa
# import soundfile as sf
# from scipy.signal import resample
# import os
# from IPython.display import Audio, display

# def simple_speed_up(input_path, output_path, speed_factor=1.5):
#     """
#     Fungsi sederhana untuk mempercepat audio
#     """
#     # Load audio
#     waveform, sr = torchaudio.load(input_path)
    
#     # Method 1: Time stretching (recommended - mempertahankan pitch)
#     audio_np = waveform.numpy()[0]
#     stretched_audio = librosa.effects.time_stretch(audio_np, rate=speed_factor)
#     result = torch.tensor(stretched_audio).unsqueeze(0)
    
#     # Save
#     torchaudio.save(output_path, result, sr)
#     print(f"Speed up audio saved: {output_path}")
    
#     return result, sr

# # Contoh penggunaan untuk satu file
# input_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/dataset-toronto/ALS/Input_Audios/A002/input_A002_02_BBP_NORMAL_segment_0.wav"
# output_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/speed_input_audio/A002_speed_1.5x.wav"

# # Buat direktori jika belum ada
# os.makedirs(os.path.dirname(output_file), exist_ok=True)

# # Speed up audio
# speed_audio, sr = simple_speed_up(input_file, output_file, speed_factor=1.5)

# # Display original vs speed up
# print("Original audio:")
# original_audio, _ = torchaudio.load(input_file)
# display(Audio(original_audio, rate=sr))

# # print("Speed up audio:")
# display(Audio(speed_audio, rate=sr))


In [14]:
# # # Simple zero-shot voice cloning dengan CosyVoice2
# import os
# import torchaudio

# # Path input dan output
# input_audio = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/speed_input_audio/A002_speed_1.5x.wav"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/exp-speed"
# os.makedirs(output_dir, exist_ok=True)

# # Text yang akan disintetis
# text_to_clone = "Even for a British Open, this is different"

# print(f"Input audio: {input_audio}")
# print(f"Text to synthesize: {text_to_clone}")

# # Load audio referensi
# rev_audio = load_wav(input_audio, 16000)
# print(f"Audio loaded: {rev_audio.shape}")

# # Lakukan inference
# output = cosyvoice.inference_zero_shot(
#     tts_text=text_to_clone,
#     prompt_text="Buy Bobby a puppy. Buy Bobby a puppy. Buy Bobby.",
#     prompt_speech_16k=rev_audio,
#     stream=False,
#     text_frontend=False,
# )

# # Simpan hasil
# for i, result in enumerate(output):
#     output_file = f'{output_dir}/A002_BBP_speed_cloned.wav'
#     torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#     print(f"Saved: {output_file}")
    
#     # Play audio (opsional)
#     from IPython.display import Audio, display
#     display(Audio(output_file))

# print("Voice cloning selesai!")

##### Concat + Speedup

In [7]:
# ## Concat audio segments and text then speed up
# import torchaudio
# import torch
# import librosa
# import os
# from IPython.display import Audio, display

# def load_speaker_texts_for_concat(annotations_file):
#     """Load teks untuk segment 0 dan 1 dari annotations file"""
#     speaker_segments = {}
#     prefix = "/home/is/lathifgalih-k/research_naist/multimodal-clone/"
    
#     with open(annotations_file, 'r', encoding='utf-8') as f:
#         for line in f:
#             if line.strip() and ("segment_0" in line or "segment_1" in line) and "BBP_NORMAL" in line.upper():
#                 parts = line.strip().split('|')
#                 if len(parts) >= 3:
#                     audio_path = parts[0]
#                     text = parts[2].strip()
                    
#                     # Extract speaker ID dan segment number
#                     filename = os.path.basename(audio_path)
#                     speaker_id = filename.split('_')[1]  # A002, A008, etc
                    
#                     if "segment_0" in filename:
#                         segment_type = "segment_0"
#                     elif "segment_1" in filename:
#                         segment_type = "segment_1"
#                     else:
#                         continue
                    
#                     if speaker_id not in speaker_segments:
#                         speaker_segments[speaker_id] = {}
                    
#                     speaker_segments[speaker_id][segment_type] = {
#                         'audio_path': os.path.join(prefix, audio_path),
#                         'text': text.replace(',', '').replace('.', '').strip()
#                     }
    
#     return speaker_segments

# def concat_audio_and_text_then_speed_up(speaker_segments, speaker_id, speed_factor=1.5):
#     """
#     Concat segment 0 dan 1 (audio + text) kemudian speed up
#     """
#     if speaker_id not in speaker_segments:
#         print(f"Speaker {speaker_id} not found!")
#         return None, None, None
    
#     segments = speaker_segments[speaker_id]
    
#     if 'segment_0' not in segments or 'segment_1' not in segments:
#         print(f"Missing segments for speaker {speaker_id}")
#         return None, None, None
    
#     # Load kedua audio
#     audio_0, sr = torchaudio.load(segments['segment_0']['audio_path'])
#     audio_1, _ = torchaudio.load(segments['segment_1']['audio_path'])
    
#     # Concat audio
#     concat_audio = torch.cat([audio_0, audio_1], dim=1)
    
#     # Concat text
#     concat_text = segments['segment_0']['text'] + " " + segments['segment_1']['text']
    
#     # Speed up using librosa
#     audio_np = concat_audio.numpy()[0]
#     stretched_audio = librosa.effects.time_stretch(audio_np, rate=speed_factor)
#     result = torch.tensor(stretched_audio).unsqueeze(0)
    
#     return result, sr, concat_text

# # Load annotations
# annotations_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/filelists/als_speaker_annotations.txt"
# speaker_segments = load_speaker_texts_for_concat(annotations_file)

# print(f"Found segments for speakers: {list(speaker_segments.keys())}")

# # Process semua speaker yang punya segment 0 dan 1
# speed_audio_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/speed_input_audio/"
# os.makedirs(speed_audio_dir, exist_ok=True)

# for speaker_id in speaker_segments.keys():
#     if 'segment_0' in speaker_segments[speaker_id] and 'segment_1' in speaker_segments[speaker_id]:
#         print(f"\nProcessing {speaker_id}...")
        
#         # Concat dan speed up
#         speed_audio, sr, concat_text = concat_audio_and_text_then_speed_up(
#             speaker_segments, speaker_id, speed_factor=1.5
#         )
        
#         if speed_audio is not None:
#             # Save speed audio
#             output_file = os.path.join(speed_audio_dir, f"{speaker_id}_concat_speed_1.5x.wav")
#             torchaudio.save(output_file, speed_audio, sr)
#             print(f"Saved: {output_file}")
#             print(f"Concatenated text: {concat_text}")
            
#             # Display audio
#             display(Audio(speed_audio, rate=sr))

In [8]:
# # Contoh untuk voice cloning dengan hasil concat
# from cosyvoice.utils.file_utils import load_wav

# # Pilih salah satu speaker untuk test voice cloning
# test_speaker = "A002"
# input_audio = f"/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/speed_input_audio/{test_speaker}_concat_speed_1.5x.wav"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/exp-concat-speed"
# os.makedirs(output_dir, exist_ok=True)

# # Voice cloning
# output = cosyvoice.inference_zero_shot(
#     tts_text="Even for a British Open, this is different",
#     prompt_text="Buy Bobby a puppy Buy Bobby a puppy Buy Bobby a puppy Buy Bobby a puppy Buy Bobby a puppy Buy Bobby",
#     prompt_speech_16k=rev_audio,
#     stream=False,
#     text_frontend=False,
# )

# # Save hasil
# for i, result in enumerate(output):
#     output_file = f'{output_dir}/{test_speaker}_concat_speed_cloned.wav'
#     torchaudio.save(output_file, result['tts_speech'], cosyvoice.sample_rate)
#     print(f"Saved: {output_file}")
    
#     # Display audio
#     display(Audio(output_file))
    
# print("Voice cloning dengan concat audio + text selesai!")

#### Denoise + No-Concat

In [13]:
# ## Zero Shot voice cloning with denoising and normalization
# import torchaudio
# import torch
# import librosa
# import os
# import numpy as np
# import noisereduce as nr
# from scipy import signal
# from IPython.display import Audio, display
# from cosyvoice.utils.file_utils import load_wav

# def denoise_audio(audio, sr):
#     """Denoise audio menggunakan noisereduce"""
#     denoised = nr.reduce_noise(y=audio, sr=sr, stationary=True, prop_decrease=0.8)
#     return denoised

# def normalize_audio(audio):
#     """Normalize audio menggunakan RMS"""
#     rms = np.sqrt(np.mean(audio ** 2))
#     if rms > 0:
#         target_rms = 10 ** (-20 / 20)  # -20dB target level
#         normalized = audio * (target_rms / rms)
#     else:
#         normalized = audio
    
#     # Clip to prevent clipping
#     normalized = np.clip(normalized, -0.95, 0.95)
#     return normalized

# def preprocess_audio(audio, sr):
#     """Complete audio preprocessing: normalize + denoise"""
#     normalized_audio = normalize_audio(audio)
#     clean_audio = denoise_audio(normalized_audio, sr)
#     return clean_audio

# def denoise_normalize_and_speed_up(input_path, output_path, speed_factor=1.5):
#     """Complete preprocessing: normalize + denoise + speed up"""
#     waveform, sr = torchaudio.load(input_path)
#     audio_np = waveform.numpy()[0]
    
#     print("Applying RMS normalization and noisereduce denoising...")
    
#     processed_audio = preprocess_audio(audio_np, sr)
    
#     print(f"Speed up with factor {speed_factor}x...")
#     stretched_audio = librosa.effects.time_stretch(processed_audio, rate=speed_factor)
    
#     result = torch.tensor(stretched_audio).unsqueeze(0)
    
#     torchaudio.save(output_path, result, sr)
#     print(f"Processed audio saved: {output_path}")
    
#     return result, sr

# def load_all_speaker_texts(annotations_file):
#     """Load semua speaker termasuk BBP_NORMAL dan A015 PATAKA"""
#     speaker_data = {}
#     prefix = "/home/is/lathifgalih-k/research_naist/multimodal-clone/"
    
#     with open(annotations_file, 'r', encoding='utf-8') as f:
#         for line in f:
#             if line.strip() and "segment_0" in line:
#                 if ("BBP_NORMAL" in line.upper()) or ("A015" in line and "PATAKA" in line.upper()):
#                     parts = line.strip().split('|')
#                     if len(parts) >= 3:
#                         audio_path = parts[0]
#                         text = parts[2].strip()
                        
#                         filename = os.path.basename(audio_path)
#                         speaker_id = filename.split('_')[1]
                        
#                         full_audio_path = os.path.join(prefix, audio_path)
#                         cleaned_text = text.replace(',', '').replace('.', '').strip()
                        
#                         speaker_data[speaker_id] = {
#                             'audio_path': full_audio_path,
#                             'text': cleaned_text
#                         }
                        
#                         print(f"Found speaker {speaker_id}: {cleaned_text}")
    
#     return speaker_data

# # Load annotations dan data speaker
# annotations_file = "/home/is/lathifgalih-k/research_naist/multimodal-clone/vits/filelists/als_speaker_annotations.txt"
# speaker_data = load_all_speaker_texts(annotations_file)

# print(f"Found {len(speaker_data)} speakers: {list(speaker_data.keys())}")

# # Setup directories
# processed_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/processed_audio/"
# output_dir = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/exp-processed/"
# os.makedirs(processed_dir, exist_ok=True)
# os.makedirs(output_dir, exist_ok=True)

# # Configuration
# text_to_clone = "Even for a British Open this is different"

# # Process all speakers
# for speaker_id, data in speaker_data.items():
#     print(f"\nProcessing {speaker_id}...")
    
#     try:
#         processed_output_file = os.path.join(processed_dir, f"{speaker_id}_processed_speed_1.5x.wav")
#         speed_audio, sr = denoise_normalize_and_speed_up(
#             data['audio_path'], 
#             processed_output_file, 
#             speed_factor=1.5
#         )
        
#         rev_audio = load_wav(processed_output_file, 16000)
#         print(f"Processed audio loaded: {rev_audio.shape}")
#         print(f"Original text: {data['text']}")
        
#         output = cosyvoice.inference_zero_shot(
#             tts_text=text_to_clone,
#             prompt_text=data['text'],
#             prompt_speech_16k=rev_audio,
#             stream=False,
#             text_frontend=False,
#         )
        
#         for i, result in enumerate(output):
#             cloned_output_file = os.path.join(output_dir, f"{speaker_id}_processed_cloned.wav")
#             torchaudio.save(cloned_output_file, result['tts_speech'], cosyvoice.sample_rate)
#             print(f"Saved: {cloned_output_file}")
            
#             print(f"Playing cloned audio for {speaker_id}:")
#             display(Audio(result['tts_speech'], rate=cosyvoice.sample_rate))
            
#     except Exception as e:
#         print(f"Error processing {speaker_id}: {e}")
#         continue

# print("Voice cloning completed!")

#### Result + Trimmed

In [12]:
# ## Post-processing trimming untuk semua hasil dengan output ke file terpisah
# import os
# import torchaudio
# from IPython.display import Audio, display

# input_folder = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/exp-processed/"
# output_folder = "/home/is/lathifgalih-k/research_naist/multimodal-clone/clone-voice-coqui/output_audio/ALS/CosyVoice2/exp-processed-trimmed/"

# # Buat direktori output jika belum ada
# os.makedirs(output_folder, exist_ok=True)

# trimming_config = {
#     "A017": 0.95,
#     "A010": 0.3,
#     "A014": 0.0,
#     "A011": 0.4,
#     "A008": 0.5,
#     "A002": 1,
#     "A016": 0.8,
#     "A006": 0.5,
#     "A015": 0.5
# }

# print("Starting post-processing trimming...")

# for filename in os.listdir(input_folder):
#     if filename.endswith(".wav"):
#         input_file_path = os.path.join(input_folder, filename)
        
#         # Extract speaker ID from filename
#         speaker_id = None
#         for sid in trimming_config.keys():
#             if sid in filename:
#                 speaker_id = sid
#                 break
        
#         if speaker_id is None:
#             print(f"Unknown speaker in file: {filename}")
#             continue
            
#         # Load original audio
#         waveform, sample_rate = torchaudio.load(input_file_path)
        
#         # Get trimming configuration
#         trim_duration = trimming_config[speaker_id]
#         start_trim = int(trim_duration * sample_rate)
        
#         print(f"Processing {filename} - Speaker: {speaker_id}, Trim: {trim_duration}s")
        
#         # Create output filename
#         base_name = os.path.splitext(filename)[0]
#         output_filename = f"{base_name}_trimmed.wav"
#         output_file_path = os.path.join(output_folder, output_filename)
        
#         # Apply trimming
#         if start_trim > 0 and start_trim < waveform.shape[1]:
#             trimmed_waveform = waveform[:, start_trim:]
            
#             # Save trimmed audio to new file
#             torchaudio.save(output_file_path, trimmed_waveform, sample_rate)
#             print(f"Trimmed and saved: {output_file_path}")
            
#             # Display trimmed audio
#             display(Audio(trimmed_waveform, rate=sample_rate))
#         else:
#             # No trimming needed, copy original file
#             torchaudio.save(output_file_path, waveform, sample_rate)
#             print(f"No trimming needed, copied: {output_file_path}")
            
#             # Display original audio
#             display(Audio(waveform, rate=sample_rate))

# print("Post-processing trimming completed!")
# print(f"Trimmed files saved to: {output_folder}")